In [1]:
from unsloth import FastLanguageModel
import torch
from datasets import load_dataset
from trl import SFTTrainer
from transformers import TrainingArguments, AutoTokenizer

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.


2025-06-15 20:37:02.871271: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1750009022.896132   66034 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1750009022.903631   66034 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1750009022.924624   66034 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1750009022.924647   66034 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1750009022.924650   66034 computation_placer.cc:177] computation placer alr

🦥 Unsloth Zoo will now patch everything to make training faster!


In [2]:
model_name = "Qwen/Qwen2.5-1.5B-Instruct"
max_seq_length = 1250

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name="Qwen/Qwen2.5-1.5B-Instruct",
    max_seq_length=max_seq_length,
    load_in_8bit=False,
    load_in_4bit=False,
    full_finetuning = False,
    device_map="auto",
)

==((====))==  Unsloth 2025.4.7: Fast Qwen2 patching. Transformers: 4.51.3.
   \\   /|    Tesla V100-SXM2-32GB. Num GPUs = 1. Max memory: 31.733 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.7.0+cu126. CUDA: 7.0. CUDA Toolkit: 12.6. Triton: 3.3.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.30. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


In [3]:
model = FastLanguageModel.get_peft_model(
    model,
    r=16,
    lora_alpha=8,
    lora_dropout=0,
    target_modules=["q_proj", "k_proj", "v_proj", "up_proj", "down_proj", "o_proj", "gate_proj"],
    use_rslora=False,
    use_gradient_checkpointing="unsloth",
    random_state=42,
    loftq_config=None,
)

print(model.print_trainable_parameters())

Unsloth 2025.4.7 patched 28 layers with 28 QKV layers, 28 O layers and 28 MLP layers.


trainable params: 18,464,768 || all params: 1,562,179,072 || trainable%: 1.1820
None


In [4]:
import json

def read_jsonl(file_name):
    with open(file_name, encoding="utf-8") as r:
        return [json.loads(line) for line in r]
        # return json.load(r)
    
data = read_jsonl("../data/train/webglm_train.jsonl")
val_data = read_jsonl("../data/test/webglm_test.jsonl")

In [5]:
data

[{'messages': [{'content': 'Ты — экспертная система Compressa RAG, предоставляющая точные и релевантные ответы на вопросы, используя только предоставленную контекстную информацию. Отвечай на русском языке.',
    'role': 'system'},
   {'content': '# Контекстная информация:\n\nИсточник [1]:\n"Машина вечного движения" перенаправляет сюда. Для других применений см. Машина вечного движения (разделение).\n\nИсточник [2]:\nК сожалению, благодаря фундаментальной физике нашей вселенной, машины вечного движения невозможны.\n\nИсточник [3]:\nТем не менее, неприкосновенность законов физики не помешала любопытным игнорировать их или пытаться их нарушить.По данным онлайн-музея Симанака, первые задокументированные машины вечного движения включали колесо, созданное индийским автором Бхаскарой в 12 веке.\n\nИсточник [4]:\nВечное движение - это движение тел, которое продолжается вечно в непоколебимой системе.Вечная машина - это гипотетическая машина, которая может работать бесконечно без внешнего источн

In [5]:
for i in data:
    print(i)
    break

{'messages': [{'content': 'i want you to act as Robert Bly and write definition of Shadow as Robert Bly', 'role': 'user'}, {'content': "As Robert Bly, I would define the Shadow as follows:\n\nThe Shadow is the hidden, repressed, or denied aspects of our personality that we've pushed into the unconscious mind. It contains the parts of ourselves that we've been taught are unacceptable or that we're ashamed of - our anger, selfishness, jealousy, or aggression. \n\nThe Shadow isn't inherently negative, though. It also holds positive qualities we've disowned, like creativity or spontaneity. It represents untapped potential and power within us.\n\nConfronting and integrating our Shadow is essential for psychological wholeness and maturity. By bringing these rejected parts of ourselves into consciousness, we can harness their energy in positive ways rather than having them erupt destructively.\n\nThe Shadow often appears in dreams or is projected onto others. Recognizing our projections and o

In [5]:
from datasets import Dataset
dataset = Dataset.from_list(data)
val_dataset = Dataset.from_list(val_data)

In [ ]:
# custom_system_message = {
#     "role": "system", 
#     "content": "Ты — экспертная система Compressa RAG. Предоставляющая точные и релевантные ответы на вопросы."
# }

# # def generate_conversation(examples):
# #     conversations = []
# #     for messages in examples["messages"]:
# #         formatted_messages = [
# #             {"role": msg["role"], "content": msg["content"]}
# #             for msg in messages
# #         ]
# #         conversations.append(formatted_messages)
# #     return {"conversations": conversations}

# def generate_conversation(examples):
#     conversations = []
#     for messages in examples["messages"]:
#         formatted_messages = [custom_system_message] + [  # <- кастомный промпт
#             {"role": msg["role"], "content": msg["content"]}
#             for msg in messages
#         ]
#         conversations.append(formatted_messages)
#     return {"conversations": conversations}

# train = tokenizer.apply_chat_template(
#     dataset.map(generate_conversation, batched=True)["conversations"],
#     tokenize=False,
# )

# val = tokenizer.apply_chat_template(
#     val_dataset.map(generate_conversation, batched=True)["conversations"],
#     tokenize=False,
# )


Map:   0%|          | 0/34640 [00:00<?, ? examples/s]

Map:   0%|          | 0/1011 [00:00<?, ? examples/s]

In [6]:
train = tokenizer.apply_chat_template(
    dataset["messages"],
    tokenize=False,
)

val = tokenizer.apply_chat_template(
    val_dataset["messages"],
    tokenize=False,
)

In [7]:
print(train[0])

<|im_start|>system
Ты — экспертная система Compressa RAG, предоставляющая точные и релевантные ответы на вопросы, используя только предоставленную контекстную информацию. Отвечай на русском языке.<|im_end|>
<|im_start|>user
# Контекстная информация:

Источник [1]:
"Машина вечного движения" перенаправляет сюда. Для других применений см. Машина вечного движения (разделение).

Источник [2]:
К сожалению, благодаря фундаментальной физике нашей вселенной, машины вечного движения невозможны.

Источник [3]:
Тем не менее, неприкосновенность законов физики не помешала любопытным игнорировать их или пытаться их нарушить.По данным онлайн-музея Симанака, первые задокументированные машины вечного движения включали колесо, созданное индийским автором Бхаскарой в 12 веке.

Источник [4]:
Вечное движение - это движение тел, которое продолжается вечно в непоколебимой системе.Вечная машина - это гипотетическая машина, которая может работать бесконечно без внешнего источника энергии.Такой тип машины невозм

In [9]:
tokens_count = 0
arr = []

for idx, line in enumerate(train):
    l = len(tokenizer.encode(line, add_special_tokens=False))
    tokens_count += l
    arr.append(l)

In [10]:
import numpy as np

arr = np.sort(np.array(arr))

In [12]:
arr

array([ 500,  521,  528, ..., 1722, 1780, 1827])

In [14]:
print(f"tokens_avg {tokens_count / len(train)}")
print(f"tokens_max {arr[-1]}")
print(f"tokens_q95 {arr[int(len(train)*0.95)]}")
print(f"tokens_q99 {arr[int(len(train)*0.99)]}")

tokens_avg 913.8981737126066
tokens_max 1827
tokens_q95 1144
tokens_q99 1250


In [15]:
len(train), len(val)

(39479, 1000)

In [7]:
import pandas as pd
from datasets import Dataset


train_tmp = pd.Series(train)
val_tmp = pd.Series(val)

train_tmp.name = "text"
val_tmp.name = "text"

train_dataset = Dataset.from_pandas(pd.DataFrame(train_tmp))
train_dataset = train_dataset.shuffle(seed = 3407)
val_dataset = Dataset.from_pandas(pd.DataFrame(val_tmp))

In [8]:
from trl import SFTTrainer, SFTConfig
trainer = SFTTrainer(
    model = model,
    tokenizer = tokenizer,
    train_dataset = train_dataset,
    eval_dataset = val_dataset,
    packing = False,
    args = SFTConfig(
        dataset_text_field = "text",
        per_device_train_batch_size = 8,
        gradient_accumulation_steps = 4,
        warmup_steps = 50,
        num_train_epochs = 1,
        learning_rate = 1e-5,
        logging_steps = 10,
        optim = "adamw_8bit",
        weight_decay = 0.01,
        lr_scheduler_type = "linear",
        seed = 3407,
        report_to="wandb",
        output_dir="qwen1_5b-v100-webglm-final",
        eval_steps=100,
        eval_strategy="steps",
        dataloader_num_workers=8,
        save_steps=75
    ),
)

Unsloth: Tokenizing ["text"] (num_proc=20):   0%|          | 0/39479 [00:00<?, ? examples/s]

Unsloth: Tokenizing ["text"] (num_proc=20):   0%|          | 0/1000 [00:00<?, ? examples/s]

In [9]:
trainer_stats = trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 39,479 | Num Epochs = 1 | Total steps = 1,233
O^O/ \_/ \    Batch size per device = 8 | Gradient accumulation steps = 4
\        /    Data Parallel GPUs = 1 | Total batch size (8 x 4 x 1) = 32
 "-____-"     Trainable parameters = 18,464,768/1,562,179,072 (1.18% trained)
wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: ERROR Failed to detect the name of this notebook. You can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: seba-vicin (seba-vicin-oxford) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


Unsloth: Will smartly offload gradients to save VRAM!


Unsloth: Not an error, but Qwen2ForCausalLM does not accept `num_items_in_batch`.
Using gradient accumulation will be very slightly less accurate.
Read more on gradient accumulation issues here: https://unsloth.ai/blog/gradient


KeyboardInterrupt: 

In [ ]:
torch.save(model.state_dict(), "qwen_3b-v100-webglm/model.pth")

In [ ]:
model.save_pretrained("qwen_3b-v100-webglm/pretrain_save")

In [11]:
with open("qwen1_5b-v100-bs_12_2-1epoch/training_stats.json", "w") as f:
    json.dump(trainer_stats, f)

In [15]:
torch.cuda.empty_cache()